In [146]:
import pandas as pd
import numpy as np
from nltk.tokenize import RegexpTokenizer
from nltk.stem import PorterStemmer
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn import metrics
import matplotlib.pyplot as plt
import seaborn as sns
pd.set_option('display.max_columns', None)
pd.set_option("display.max_rows", None)
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import LabelEncoder, StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, classification_report

In [147]:
attorneyDF = pd.read_csv("attorneys.csv")
attorneytimeDF = pd.read_csv("attorneytimeentries.csv")
categoriesDF = pd.read_csv("categories.csv")
clientsDF = pd.read_csv("clients.csv")
questionpostsDF = pd.read_csv("questionposts_corrected_full.csv")
questionsDF = pd.read_csv("questions.csv")
statesitesDF = pd.read_csv("statesites.csv")
subcategoriesDF = pd.read_csv("subcategories.csv")
all_questions_df = pd.read_csv("All_data.csv")

In [148]:

columns = ['Id', 'StateAbbr', 'QuestionUno', 'CategoryUno', 'Category',
       'SubcategoryUno', 'Subcategory', 'ClientUno', 'AskedOnUtc',
       'TakenByAttorneyUno', 'TakenOnUtc', 'ClosedByAttorneyUno',
       'ClosedOnUtc', 'LegalDeadline']
questionsDF.columns = columns
questionsDF.head()
questionsDF.shape

(202879, 14)

In [149]:
statesitesDF.head()

Id StateAbbr    StateName  AllowedAssets  BaseIncomeLimit  \
0   1        AL      Alabama          10000            13590   
1   2        AR     Arkansas          10000            13590   
2   3        AZ      Arizona          10000            13590   
3   4        CA   California          10000            13590   
4   5        CT  Connecticut          10000            13590   

   PerHouseholdMemberIncomeLimit  IncomeMultiplier  
0                           4720               2.5  
1                           4720               2.5  
2                           4720               2.5  
3                           4720               4.0  
4                           4720               2.5

In [150]:
subcategoriesDF.head()

Id StateAbbr                           CategoryUno  \
0   1        AK  2D43B4FD-FAC8-47C3-A891-085F5D74D64B   
1   2        AK  2D43B4FD-FAC8-47C3-A891-085F5D74D64B   
2   3        AK  2D43B4FD-FAC8-47C3-A891-085F5D74D64B   
3   4        AK  D3504F18-AC99-408B-B1D2-230DC130F9EC   
4   5        AK  BF144F3C-5743-47C5-9EEB-418FF0FAF0D8   

                         SubcategoryUno                   Subcategory  
0  546C6AD6-4D2B-4B1D-B09F-8016C5B02D66              COVID-19-Housing  
1  572148E8-96C7-4B74-8280-B749191C5B4C            COVID-19-Insurance  
2  5AA5088E-3A9D-4D99-B6FE-69122C34194A       COVID-19-Lost Documents  
3  E5DF5CEB-649F-47B3-B665-1BEB3EA4AD42  Emancipation and Delinquency  
4  16E4350E-BC59-40B7-BF72-0BC225ECA4D1                   Immigration

In [151]:
all_questions_df.head()

Id_x StateAbbr_x                           QuestionUno  \
0     1          NC  BB53B2A4-7C1B-45C3-9693-62047889317D   
1     2          NC  0C49F841-2782-4313-961E-7882B96D0854   
2     3          NC  BFC28E08-B6B1-4185-A91A-89DF90816BE4   
3     4          NC  45B24109-243A-489B-B0D2-2F36C2A369FE   
4     5          NC  C4707F71-FE4A-4154-8174-AF00BEE2B361   

                            CategoryUno                      Category  \
0  C932D197-7F43-4BCF-BE0B-FE5F5DBCB9EF           Family and Children   
1  C8E1275A-6C42-42E4-9B7D-231BAC438FC9             Individual Rights   
2  C8E1275A-6C42-42E4-9B7D-231BAC438FC9             Individual Rights   
3  C932D197-7F43-4BCF-BE0B-FE5F5DBCB9EF           Family and Children   
4  F6016FBD-9501-4448-BCD3-BBB0E834E33B  Consumer Financial Questions   

                         SubcategoryUno  \
0  E9F87919-0CD5-4D9D-AAC6-3CBC49132F1D   
1  73A59926-BA0B-44EC-ABF3-F4C9181EEA83   
2  73A59926-BA0B-44EC-ABF3-F4C9181EEA83   
3  E9F87919-0CD5-4D9D-AAC6-3CBC49132F1D   
4  73FE486E-2B51-456A-A6D9-78A7D05802AA   

                                       Subcategory  \
0  Family/Divorce/Custody/Visitation/Child Support   
1                      Civil/Constitutional Rights   
2                      Civil/Constitutional Rights   
3  Family/Divorce/Custody/Visitation/Child Support   
4                    Bankruptcy, Debts & Purchases   

                              ClientUno           AskedOnUtc  \
0  9C35423C-914A-42BC-8EBC-A370E76E2178  2019-06-19 22:10:06   
1  DF636AEE-7D08-4F90-9A5C-0A2A726C6B59  2019-06-19 23:34:36   
2  DF636AEE-7D08-4F90-9A5C-0A2A726C6B59  2019-06-19 23:57:18   
3  C9C3FA40-0D60-49B9-97F1-63AFEFAFA484  2019-06-20 02:33:14   
4  ED7DEA10-CDB7-4A05-891D-889D1EA710BE  2019-06-20 17:04:47   

                     TakenByAttorneyUno           TakenOnUtc  \
0                                   NaN                  NaN   
1                                   NaN                  NaN   
2  FA34142B-1575-4720-981C-2D28C3560137  2019-06-22 02:37:16   
3  FA34142B-1575-4720-981C-2D28C3560137  2019-07-27 18:04:08   
4                                   NaN                  NaN   

                    ClosedByAttorneyUno          ClosedOnUtc  \
0                                   NaN  2019-08-13 15:09:06   
1                                   NaN  2019-08-13 15:09:14   
2  FA34142B-1575-4720-981C-2D28C3560137  2019-06-24 19:02:35   
3  FA34142B-1575-4720-981C-2D28C3560137  2019-07-31 05:49:18   
4                                   NaN  2019-08-13 15:09:20   

         LegalDeadline   Id_y StateAbbr_y      County       StateName  \
0  2019-07-08 00:00:00  87804          NC  Cumberland  North Carolina   
1                  NaN  87825          NC     Forsyth  North Carolina   
2                  NaN  87825          NC     Forsyth  North Carolina   
3                  NaN  87748          NC       Rowan  North Carolina   
4                  NaN  87868          NC        Wake  North Carolina   

   PostalCode         EthnicIdentity   Age  Gender        MaritalStatus  \
0     28301.0       African American  26.0  Female               Single   
1     27127.0  I'd rather not answer  41.0    Male  Divorced or Widowed   
2     27127.0  I'd rather not answer  41.0    Male  Divorced or Widowed   
3     28081.0                  Asian  45.0  Female  Married / remarried   
4     27513.0       African American  27.0  Female  Divorced or Widowed   

  Veteran Imprisoned  NumberInHousehold  AnnualIncome  AllowedIncome  \
0      No         No                3.0           0.0        41910.0   
1      No         No                4.0        9240.0        56070.0   
2      No         No                4.0        9240.0        56070.0   
3      No         No                2.0        1600.0        27750.0   
4      No         No                2.0       12000.0        27750.0   

   CheckingBalance  SavingsBalance  InvestmentsBalance         CreatedUtc_x  \
0              0.0             NaN                 NaN  

In [152]:
all_questions_df_20k = all_questions_df.sample(n = 20000)
all_questions_df_20k.shape


(20000, 37)

In [239]:
X = all_questions_df.drop(['Id_x', 'QuestionUno','CategoryUno', "SubcategoryUno", 'Subcategory', "ClientUno", "TakenByAttorneyUno", "ClosedByAttorneyUno", "Id_y", "StateAbbr_y", "StateName", "Unnamed: 0", "Id", "StateAbbr", "PostText", "AskedOnUtc", "TakenOnUtc", "ClosedOnUtc", "LegalDeadline", "PostalCode", "County", "AllowedIncome", "InvestmentsBalance", "CreatedUtc_x", "CreatedUtc_y", "SavingsBalance"], axis=1)
X.head()



StateAbbr_x                      Category         EthnicIdentity   Age  \
0          NC           Family and Children       African American  26.0   
1          NC             Individual Rights  I'd rather not answer  41.0   
2          NC             Individual Rights  I'd rather not answer  41.0   
3          NC           Family and Children                  Asian  45.0   
4          NC  Consumer Financial Questions       African American  27.0   

   Gender        MaritalStatus Veteran Imprisoned  NumberInHousehold  \
0  Female               Single      No         No                3.0   
1    Male  Divorced or Widowed      No         No                4.0   
2    Male  Divorced or Widowed      No         No                4.0   
3  Female  Married / remarried      No         No                2.0   
4  Female  Divorced or Widowed      No         No                2.0   

   AnnualIncome  CheckingBalance  
0           0.0              0.0  
1        9240.0             26.0  
2        9240.0             26.0  
3        1600.0           1600.0  
4       12000.0             50.0

In [240]:
tokenizer = RegexpTokenizer('[a-z]+')
stemmer = PorterStemmer()
stop_words = set(stopwords.words("english"))

def preprocess(s):
    if isinstance(s, str):  # check if s is a non-empty string
        w = tokenizer.tokenize(s.lower())         
        w = [word for word in w if word not in stop_words]    
        w = [stemmer.stem(word) for word in w]    
        return ' '.join(w)
    else:
        return ''  # return an empty string if s is empty or not a string

all_questions_df_20k['text'] = all_questions_df_20k['PostText'].apply(preprocess)


In [241]:
all_questions_df_20k.head()

Id_x StateAbbr_x                           QuestionUno  \
144986  178213          TN  6E098FD0-95AB-45B1-B87C-C138DE3F775D   
59958    70178          TX  0468CB68-E04E-49ED-9F5C-215D0E30C33B   
79338    93166          TX  56D7E103-D2B2-446C-9079-0EB7EEC0C0A4   
158259  192953          FL  9BCDBCB6-FD7F-4AA1-B545-671207A4A271   
34147    37439          FL  45B9F801-FFD1-48FD-BED4-082116E82DC7   

                                 CategoryUno             Category  \
144986  82237E76-8369-40D9-B649-C7B506FED1C5  Family and Children   
59958   CD9242A3-3478-4311-A951-F42ECB1D978D  Family and Children   
79338   7C8440D2-577D-4CB4-BF62-CE305536A3DB                Other   
158259  04F9F18F-45B6-40A9-A092-DF25C636F472  Family and Children   
34147   54C694DD-F7C2-45D3-B82C-34FFB3085716                Other   

                              SubcategoryUno                      Subcategory  \
144986  ED1335C0-5FCA-457C-BB3E-9E094DEA4E33           Family/Divorce/Custody   
59958   0058D8C8-7E5B-4123-A8CB-E4F2B19C4F67  Family/Divorce/Custody/Adoption   
79338   49F13E4A-F383-4F88-9983-1FBE5810D34C                         Business   
158259  86FD89F6-135F-44E0-8809-54039BF8C31A           Family/Divorce/Custody   
34147   A08B92E0-884C-4CE6-ABF2-571086D940BF                            Other   

                                   ClientUno           AskedOnUtc  \
144986  6740C8F1-689C-4846-9AE0-F1208E50B534  2020-01-05 04:48:13   
59958   2A0252C0-6F9C-4583-9D72-86D754579E88  2020-06-07 17:46:01   
79338   024F000E-A806-43E3-8DBE-EB51E72C274F  2021-07-15 14:21:47   
158259  9EAF38F1-09B8-4B46-AAC6-A16E7BC52753  2020-06-04 17:30:35   
34147   E4BA0E4A-A8B4-49F2-AF5B-FC4327C68329  2021-10-08 17:53:10   

                          TakenByAttorneyUno           TakenOnUtc  \
144986  775743CD-AE89-4866-A5A3-0DDEF53E619F  2020-01-16 21:50:35   
59958                                    NaN                  NaN   
79338   632EE095-E1C4-4428-8285-FCE7D1FECC21  2021-07-30 15:48:51   
158259  EB1EEEC7-AB79-4434-BA83-D77AFE1F1635  2020-06-04 18:25:19   
34147   EB1EEEC7-AB79-4434-BA83-D77AFE1F1635  2021-10-08 18:10:05   

                         ClosedByAttorneyUno          ClosedOnUtc  \
144986  775743CD-AE89-4866-A5A3-0DDEF53E619F  2020-01-23 20:22:02   
59958                                    NaN  2020-08-30 14:10:26   
79338   632EE095-E1C4-4428-8285-FCE7D1FECC21  2021-08-09 15:57:19   
158259  EB1EEEC7-AB79-4434-BA83-D77AFE1F1635  2020-06-09 15:10:49   
34147   EB1EEEC7-AB79-4434-BA83-D77AFE1F1635  2021-10-18 14:32:39   

              LegalDeadline    Id_y StateAbbr_y    County  StateName  \
144986                  NaN  219216          TN    Shelby  Tennessee   
59958   2020-06-08 00:00:00  279905          TX   Midland      Texas   
79338   2021-08-22 00:00:00  314775          TX    Travis      Texas   
158259                  NaN  266828          FL    Orange    Florida   
34147                   NaN  323639          FL  Seminole    Florida   

        PostalCode          EthnicIdentity   Age  Gender  \
144986     38053.0        African American  55.0    Male   
59958      79703.0      Latino or Hispanic  34.0  Female   
79338      78747.0      Latino or Hispanic  23.0    Male   
158259     32821.0      Latino or Hispanic  33.0  Female   
34147      32707.0  Not Hispanic or Latino  71.0  Female   

                MaritalStatus Veteran Imprisoned  NumberInHousehold  \
144986              Separated      No         No                1.0   
59958     Married / remarried      No         No                5.0   
79338                  Single      No         No                2.0   
158259  I'd rather not answer      No         No                4.0   
34147                Divorced      No         No                1.0   

        AnnualIncome  AllowedIncome  CheckingBalance  SavingsBalance  \
144986        1300.0        13590.0             55.0             NaN   
59958        21000.0        60790.0              NaN             NaN   
79338           6

In [283]:
X = all_questions_df_20k.drop(['Id_x', 'QuestionUno','CategoryUno', "SubcategoryUno", 'Subcategory', "ClientUno", "TakenByAttorneyUno", "ClosedByAttorneyUno", "Id_y", "StateAbbr_y", "StateName", "Unnamed: 0", "Id", "StateAbbr", "PostText", "AskedOnUtc", "TakenOnUtc", "ClosedOnUtc", "LegalDeadline", "PostalCode", "County", "AllowedIncome", "InvestmentsBalance", "CreatedUtc_x", "CreatedUtc_y", "SavingsBalance"], axis=1)


In [284]:
X.head()

StateAbbr_x             Category          EthnicIdentity   Age  Gender  \
144986          TN  Family and Children        African American  55.0    Male   
59958           TX  Family and Children      Latino or Hispanic  34.0  Female   
79338           TX                Other      Latino or Hispanic  23.0    Male   
158259          FL  Family and Children      Latino or Hispanic  33.0  Female   
34147           FL                Other  Not Hispanic or Latino  71.0  Female   

                MaritalStatus Veteran Imprisoned  NumberInHousehold  \
144986              Separated      No         No                1.0   
59958     Married / remarried      No         No                5.0   
79338                  Single      No         No                2.0   
158259  I'd rather not answer      No         No                4.0   
34147                Divorced      No         No                1.0   

        AnnualIncome  CheckingBalance  \
144986        1300.0             55.0   
59958        21000.0              NaN   
79338           65.0            500.0   
158259       24588.0            127.0   
34147        22800.0            902.0   

                                                     text  
144986  complet uncontest divorc paper local legal ser...  
59958   find abus neglect judg made evid support alleg...  
79338   nd move compani pick stuff mover paperwork sai...  
158259  file divorc orang counti dissolut minor childr...  
34147   princip tell bank accept durabl power attorney...

In [285]:
X = X.dropna()

In [286]:
X = X.reset_index(drop=True)

In [287]:
X.head()

StateAbbr_x                  Category          EthnicIdentity   Age  Gender  \
0          TN       Family and Children        African American  55.0    Male   
1          TX                     Other      Latino or Hispanic  23.0    Male   
2          FL       Family and Children      Latino or Hispanic  33.0  Female   
3          FL                     Other  Not Hispanic or Latino  71.0  Female   
4          TN  Housing and Homelessness               Caucasian  28.0    Male   

           MaritalStatus Veteran Imprisoned  NumberInHousehold  AnnualIncome  \
0              Separated      No         No                1.0        1300.0   
1                 Single      No         No                2.0          65.0   
2  I'd rather not answer      No         No                4.0       24588.0   
3               Divorced      No         No                1.0       22800.0   
4    Married / remarried     Yes         No                4.0       55000.0   

   CheckingBalance                                               text  
0             55.0  complet uncontest divorc paper local legal ser...  
1            500.0  nd move compani pick stuff mover paperwork sai...  
2            127.0  file divorc orang counti dissolut minor childr...  
3            902.0  princip tell bank accept durabl power attorney...  
4            300.0  late pay juli rent landlord file lawsuit month...

In [288]:
X['EthnicIdentity'] = X['EthnicIdentity'].str.replace('Latino or Hispanic|Hispanic or Latino', 'Hispanic')

ethnicities = ["Caucasian", "African American", "Hispanic", "Not Hispanic", "Asian"]
X = X[X['EthnicIdentity'].isin(ethnicities)]
X.head()

value_counts = X.MaritalStatus.value_counts()
value_counts


/var/folders/s1/yfb6gczs3_zgkckzr8245jpm0000gn/T/ipykernel_7535/1065396466.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  X['EthnicIdentity'] = X['EthnicIdentity'].str.replace('Latino or Hispanic|Hispanic or Latino', 'Hispanic')


Single                   4504
Married / remarried      2608
Divorced or Widowed      2001
Separated                1096
Married                   344
Divorced                  244
I'd rather not answer     203
Widowed                    39
Name: MaritalStatus, dtype: int64

In [289]:

X['MaritalStatus'] = X['MaritalStatus'].str.replace('Married / remarried', 'Married')
X['MaritalStatus'] = X['MaritalStatus'].str.replace('Widowed', 'Divorced')
X['MaritalStatus'] = X['MaritalStatus'].str.replace('Divorced or Widowed', 'Divorced')
X['MaritalStatus'] = X['MaritalStatus'].str.replace('Divorced or Divorced', 'Divorced')

X['MaritalStatus'] = X['MaritalStatus'].str.replace('Married', 'Married / remarried')
X['MaritalStatus'] = X['MaritalStatus'].str.replace('Divorced', 'Divorced or Widowed')

value_counts = X.MaritalStatus.value_counts()
value_counts

Single                   4504
Married / remarried      2952
Divorced or Widowed      2284
Separated                1096
I'd rather not answer     203
Name: MaritalStatus, dtype: int64

In [290]:
X.columns

Index(['StateAbbr_x', 'Category', 'EthnicIdentity', 'Age', 'Gender',
       'MaritalStatus', 'Veteran', 'Imprisoned', 'NumberInHousehold',
       'AnnualIncome', 'CheckingBalance', 'text'],
      dtype='object')

In [291]:
columns = ['state',"Category", 'ethnicity', 'age', 'gender', 'maritalStatus',
       'veteran', 'imprisoned', 'numInHouse', 'annualIncome',
       'CheckingBalance', 'text']
X.columns = columns
X.head()

state                  Category         ethnicity   age  gender  \
0    TN       Family and Children  African American  55.0    Male   
1    TX                     Other          Hispanic  23.0    Male   
2    FL       Family and Children          Hispanic  33.0  Female   
3    FL                     Other      Not Hispanic  71.0  Female   
4    TN  Housing and Homelessness         Caucasian  28.0    Male   

           maritalStatus veteran imprisoned  numInHouse  annualIncome  \
0              Separated      No         No         1.0        1300.0   
1                 Single      No         No         2.0          65.0   
2  I'd rather not answer      No         No         4.0       24588.0   
3    Divorced or Widowed      No         No         1.0       22800.0   
4    Married / remarried     Yes         No         4.0       55000.0   

   CheckingBalance                                               text  
0             55.0  complet uncontest divorc paper local legal ser...  
1            500.0  nd move compani pick stuff mover paperwork sai...  
2            127.0  file divorc orang counti dissolut minor childr...  
3            902.0  princip tell bank accept durabl power attorney...  
4            300.0  late pay juli rent landlord file lawsuit month...

In [292]:
state_codes, unique_state = X['state'].factorize()
X["state"] = state_codes
state_dict = {key: value for key, value in zip(unique_state, state_codes)}

In [293]:
ethnicity_codes, unique_ethnicity = X['ethnicity'].factorize()
X["ethnicity"] = ethnicity_codes
ethnicity_dict = {key: value for key, value in zip(unique_ethnicity, ethnicity_codes)}
X.head()

state                  Category  ethnicity   age  gender  \
0      0       Family and Children          0  55.0    Male   
1      1                     Other          1  23.0    Male   
2      2       Family and Children          1  33.0  Female   
3      2                     Other          2  71.0  Female   
4      0  Housing and Homelessness          3  28.0    Male   

           maritalStatus veteran imprisoned  numInHouse  annualIncome  \
0              Separated      No         No         1.0        1300.0   
1                 Single      No         No         2.0          65.0   
2  I'd rather not answer      No         No         4.0       24588.0   
3    Divorced or Widowed      No         No         1.0       22800.0   
4    Married / remarried     Yes         No         4.0       55000.0   

   CheckingBalance                                               text  
0             55.0  complet uncontest divorc paper local legal ser...  
1            500.0  nd move compani pick stuff mover paperwork sai...  
2            127.0  file divorc orang counti dissolut minor childr...  
3            902.0  princip tell bank accept durabl power attorney...  
4            300.0  late pay juli rent landlord file lawsuit month...

In [294]:
gender_codes, unique_gender = X['gender'].factorize()
X["gender"] = gender_codes
gender_dict = {key: value for key, value in zip(unique_gender, gender_codes)}
X.head()

state                  Category  ethnicity   age  gender  \
0      0       Family and Children          0  55.0       0   
1      1                     Other          1  23.0       0   
2      2       Family and Children          1  33.0       1   
3      2                     Other          2  71.0       1   
4      0  Housing and Homelessness          3  28.0       0   

           maritalStatus veteran imprisoned  numInHouse  annualIncome  \
0              Separated      No         No         1.0        1300.0   
1                 Single      No         No         2.0          65.0   
2  I'd rather not answer      No         No         4.0       24588.0   
3    Divorced or Widowed      No         No         1.0       22800.0   
4    Married / remarried     Yes         No         4.0       55000.0   

   CheckingBalance                                               text  
0             55.0  complet uncontest divorc paper local legal ser...  
1            500.0  nd move compani pick stuff mover paperwork sai...  
2            127.0  file divorc orang counti dissolut minor childr...  
3            902.0  princip tell bank accept durabl power attorney...  
4            300.0  late pay juli rent landlord file lawsuit month...

In [295]:
marital_codes, unique_marital = X['maritalStatus'].factorize()
X["maritalStatus"] = marital_codes
marital_dict = {key: value for key, value in zip(unique_marital, marital_codes)}
X.head()

state                  Category  ethnicity   age  gender  maritalStatus  \
0      0       Family and Children          0  55.0       0              0   
1      1                     Other          1  23.0       0              1   
2      2       Family and Children          1  33.0       1              2   
3      2                     Other          2  71.0       1              3   
4      0  Housing and Homelessness          3  28.0       0              4   

  veteran imprisoned  numInHouse  annualIncome  CheckingBalance  \
0      No         No         1.0        1300.0             55.0   
1      No         No         2.0          65.0            500.0   
2      No         No         4.0       24588.0            127.0   
3      No         No         1.0       22800.0            902.0   
4     Yes         No         4.0       55000.0            300.0   

                                                text  
0  complet uncontest divorc paper local legal ser...  
1  nd move compani pick stuff mover paperwork sai...  
2  file divorc orang counti dissolut minor childr...  
3  princip tell bank accept durabl power attorney...  
4  late pay juli rent landlord file lawsuit month...

In [296]:
veteran_codes, unique_veteran = X['veteran'].factorize()
X["veteran"] = veteran_codes
veteran_dict = {key: value for key, value in zip(unique_veteran, veteran_codes)}
X.head()

state                  Category  ethnicity   age  gender  maritalStatus  \
0      0       Family and Children          0  55.0       0              0   
1      1                     Other          1  23.0       0              1   
2      2       Family and Children          1  33.0       1              2   
3      2                     Other          2  71.0       1              3   
4      0  Housing and Homelessness          3  28.0       0              4   

   veteran imprisoned  numInHouse  annualIncome  CheckingBalance  \
0        0         No         1.0        1300.0             55.0   
1        0         No         2.0          65.0            500.0   
2        0         No         4.0       24588.0            127.0   
3        0         No         1.0       22800.0            902.0   
4        1         No         4.0       55000.0            300.0   

                                                text  
0  complet uncontest divorc paper local legal ser...  
1  nd move compani pick stuff mover paperwork sai...  
2  file divorc orang counti dissolut minor childr...  
3  princip tell bank accept durabl power attorney...  
4  late pay juli rent landlord file lawsuit month...

In [297]:
imprison_codes, unique_imprison = X['imprisoned'].factorize()
X["imprisoned"] = imprison_codes
imprison_dict = {key: value for key, value in zip(unique_imprison,imprison_codes)}
X.head()

state                  Category  ethnicity   age  gender  maritalStatus  \
0      0       Family and Children          0  55.0       0              0   
1      1                     Other          1  23.0       0              1   
2      2       Family and Children          1  33.0       1              2   
3      2                     Other          2  71.0       1              3   
4      0  Housing and Homelessness          3  28.0       0              4   

   veteran  imprisoned  numInHouse  annualIncome  CheckingBalance  \
0        0           0         1.0        1300.0             55.0   
1        0           0         2.0          65.0            500.0   
2        0           0         4.0       24588.0            127.0   
3        0           0         1.0       22800.0            902.0   
4        1           0         4.0       55000.0            300.0   

                                                text  
0  complet uncontest divorc paper local legal ser...  
1  nd move compani pick stuff mover paperwork sai...  
2  file divorc orang counti dissolut minor childr...  
3  princip tell bank accept durabl power attorney...  
4  late pay juli rent landlord file lawsuit month...

In [298]:
X['Category'] = X['Category'].str.replace('Juvenile|Education|Income Maintenance|Health and Disability', 'Other')
X = X[X.Category != 'Other']

value_counts = X.Category.value_counts()
value_counts

/var/folders/s1/yfb6gczs3_zgkckzr8245jpm0000gn/T/ipykernel_7535/3605086480.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  X['Category'] = X['Category'].str.replace('Juvenile|Education|Income Maintenance|Health and Disability', 'Other')


Family and Children                  4646
Housing and Homelessness             2002
Consumer Financial Questions         1004
Work, Employment and Unemployment     629
Individual Rights                     406
Name: Category, dtype: int64

In [299]:
category_codes, unique_category = X['Category'].factorize()
X["Category"] = category_codes
category_dict = {key: value for key, value in zip(unique_category,category_codes)}
X.head()
X.reset_index()

index  state  Category  ethnicity    age  gender  maritalStatus  \
0         0      0         0          0   55.0       0              0   
1         2      2         0          1   33.0       1              2   
2         4      0         1          3   28.0       0              4   
3         5      2         0          3   30.0       1              3   
4         6      3         0          3   40.0       1              0   
5         8      5         2          3   63.0       1              1   
6        10      6         3          0   39.0       0              1   
7        11      7         0          3   62.0       0              1   
8        13      9         1          3   59.0       1              1   
9        16      3         1          3   31.0       1              3   
10       18      7         0          3   47.0       1              0   
11       20      5         3          3   45.0       1              3   
12       22      5         2          0   47.0       0              1   
13       23     10         3          3   55.0       0              4   
14       24      9         0          0   33.0       1              0   
15       25      9         0          1   46.0       1              3   
16       27      5         1          3   36.0       0              1   
17       28      2         0          3   35.0       1              0   
18       29      1         2          3   30.0       0              1   
19       30     11         0          3   58.0       1              4   
20       31     12         0          2   37.0       0              4   
21       32      4         3          3   37.0       1              4   
22       34     14         0          3   35.0       1              4   
23       39      6         4          2   24.0       1              1   
24       42      9         0          3   40.0       0              4   
25       43      4         2          1   33.0       0              1   
26       44     15         0          3   22.0       1              1   
27       45     12         2          1   38.0       1              4   
28       46      2         2          1   42.0       1              1   
29       47      4         2          3   57.0       1              4   
30       50     16         1          3   39.0       0              1   
31       52      3         0          3   33.0       1              1   
32       56     18         2          0   40.0       0              4   
33       58     13         1          3   41.0       1              1   
34       59      3         0          3   28.0       1              3   
35       60      4         2          3   20.0       0              1   
36       61      2         0          3   23.0       1              0   
37       64     20         0          3   37.0       1              3   
38       66      5         1          3   32.0       1              0   
39       67      5         0          3   38.0       0              1   
40       69      2         0          3   35.0       1              0   
41       73      1         1          3   51.0       1              3   
42       75      2         1          3   64.0       0              3   
43       77      2         0          1   27.0       1              4   
44       79     16         1          3   35.0       1              4   
45       81     21         0          1   36.0       0              4   
46       83     22         0          3   30.0       1              3   
47       86      5         1          4   23.0       1              1   
48       87      6         4          3   42.0       1              3   
49       89     24         3          3   22.0       1              1   
50       90      0         0          0   51.0       1              0   
51       92      6         0          3   61.0       0              4   
52       93      3         3          3   25.0       1              1   
53       95     16         0          3   26.0       1          

In [300]:
y = X.Category
X = X.drop("Category", axis=1)

In [302]:
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report

# Convert text column into numerical vectors
vectorizer = CountVectorizer()
X_text = vectorizer.fit_transform(X['text'])

# Combine text vectors with other input variables
X_input = X.drop('text', axis=1)
X_input = np.hstack((X_input, X_text.toarray()))

# Split the dataset into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_input, y, test_size=0.2, random_state=42)


# Train and evaluate the Random Forest classifier
rfc = RandomForestClassifier()
rfc.fit(X_train, y_train)
y_pred_rfc = rfc.predict(X_test)
acc_rfc = accuracy_score(y_test, y_pred_rfc)
print("Random Forest Accuracy:", acc_rfc)

Random Forest Accuracy: 0.8141542002301496
